In [1]:
import os
import numpy as np
import cv2
import tensorflow as tf
import pandas as pd
import PIL
import scipy.sparse as sp
import resource
import time
from PIL import Image
from PIL import ImageFile
from sklearn.model_selection import train_test_split, KFold, StratifiedKFold
from sklearn.utils import class_weight
from sklearn.metrics import classification_report
import json

In [2]:
import re
import pandas
import numpy as np
from nltk.corpus import stopwords
from tensorflow.python.keras.preprocessing.text import Tokenizer
from nltk.corpus import names
from nltk.stem import WordNetLemmatizer

In [3]:
import warnings 
warnings.filterwarnings(action='ignore')

In [7]:
def set_env():
    os.environ['CUDA_VISIBLE_DEVICES'] = '0'
    config = tf.ConfigProto()
    config.gpu_options.per_process_gpu_memory_fraction = 0.75
    session = tf.Session(config=config)
    session
set_env()

## kfold

In [4]:
num = 5

In [5]:
#skf = StratifiedKFold(n_splits=num)

In [6]:
kf = KFold(n_splits=num, random_state=None, shuffle=False) # default -> 5 times

In [8]:
# 데이터 불러오기
df=pd.read_csv("book_data_final.csv", encoding='ISO-8859-1')

# review, label의 nan값 행렬 삭제
df.dropna(inplace=True,subset=["review", "label"])
df.reset_index(drop=True,inplace=True)

In [9]:
df

number                                             review  \
0           0  hollow ever gone tourist thinking finally goin...   
1           1  monotonous dragging pace feel like reading boo...   
2           2  much complex romance human devil act larue mak...   
3           3  invisible interest bought book based bought bo...   
4           4  even though really wish book wa solidly good y...   
...       ...                                                ...   
82511   82619  naked raw cover tricked read lot anthology tho...   
82512   82620  better le great buying book based love poetry ...   
82513   82621  picked book fell love book feel like came sike...   
82514   82622  much like crush think volume going stay much l...   
82515   82623  siken incredible follow poetry siken incredibl...   

                                                   title         author  \
0                      The Invisible Life of Addie LaRue   V. E. Schwab   
1                      The Invisible Life of Addie LaRue   V. E. Schwab   
2                      The Invisible Life of Addie LaRue   V. E. Schwab   
3                      The Invisible Life of Addie LaRue   V. E. Schwab   
4      A Court of Silver Flames (A Court of Thorns an...  Sarah J. Maas   
...                                                  ...            ...   
82511                                   War of the Foxes  Richard Siken   
82512                                   War of the Foxes  Richard Siken   
82513                                   War of the Foxes  Richard Siken   
82514                                   War of the Foxes  Richard Siken   
82515                                   War of the Foxes  Richard Siken   

                                publisher  \
0          Tor Books; Illustrated edition   
1          Tor Books; Illustrated edition   
2          Tor Books; Illustrated edition   
3          Tor Books; Illustrated edition   
4      Bloomsbury Publishing; 1st edition   
...                                   ...   
82511                 Copper Canyon Press   
82512                 Copper Canyon Press   
82513                 Copper Canyon Press   
82514                 Copper Canyon Press   
82515                 Copper Canyon Press   

                                                 img_url  label  \
0      https://images-na.ssl-images-amazon.com/images...      2   
1      https://images-na.ssl-images-amazon.com/images...      2   
2      https://images-na.ssl-images-amazon.com/images...      5   
3      https://images-na.ssl-images-amazon.com/images...      1   
4      https://images-na.ssl-images-amazon.com/images...      4   
...                                                  ...    ...   
82511  https://images-na.ssl-images-amazon.com/images...      5   
82512  https://images-na.ssl-images-amazon.com/images...      4   
82513  https://images-na.ssl-images-amazon.com/images...      2   
82514  https://images-na.ssl-images-amazon.com/images...      5   
82515  https://images-na.ssl-images-amazon.com/images...      5   

                                            id  
0      51FVPBt51ZL._SX329_BO1,204,203,200_.jpg  
1      51FVPBt51ZL._SX329_BO1,204,203,200_.jpg  
2      51FVPBt51ZL._SX329_BO1,204,203,200_.jpg  
3      51FVPBt51ZL._SX329_BO1,204,203,200_.jpg  
4      51nYjtfGQnL._SY344_BO1,204,203,200_.jpg  
...                                        ...  
82511  51qAZy-xFtL._SY344_BO1,204,203,200_.jpg  
82512  51qAZy-xFtL._SY344_BO1,204,203,200_.jpg  
82513  51qAZy-xFtL._SY344_BO1,204,203,200_.jpg  
82514  51qAZy-xFtL._SY344_BO1,204,203,200_.jpg  
82515  51qAZy-xFtL._SY344_BO1,204,203,200_.jpg  

[82516 rows x 8 columns]

In [10]:
# index와 number를 동일하게
# max_data = 100
# df = df.iloc[:max_data]
for i in range(len(df["number"])):
    if i != df["number"][i]:
        df["number"][i] = i

In [11]:
df

number                                             review  \
0           0  hollow ever gone tourist thinking finally goin...   
1           1  monotonous dragging pace feel like reading boo...   
2           2  much complex romance human devil act larue mak...   
3           3  invisible interest bought book based bought bo...   
4           4  even though really wish book wa solidly good y...   
...       ...                                                ...   
82511   82511  naked raw cover tricked read lot anthology tho...   
82512   82512  better le great buying book based love poetry ...   
82513   82513  picked book fell love book feel like came sike...   
82514   82514  much like crush think volume going stay much l...   
82515   82515  siken incredible follow poetry siken incredibl...   

                                                   title         author  \
0                      The Invisible Life of Addie LaRue   V. E. Schwab   
1                      The Invisible Life of Addie LaRue   V. E. Schwab   
2                      The Invisible Life of Addie LaRue   V. E. Schwab   
3                      The Invisible Life of Addie LaRue   V. E. Schwab   
4      A Court of Silver Flames (A Court of Thorns an...  Sarah J. Maas   
...                                                  ...            ...   
82511                                   War of the Foxes  Richard Siken   
82512                                   War of the Foxes  Richard Siken   
82513                                   War of the Foxes  Richard Siken   
82514                                   War of the Foxes  Richard Siken   
82515                                   War of the Foxes  Richard Siken   

                                publisher  \
0          Tor Books; Illustrated edition   
1          Tor Books; Illustrated edition   
2          Tor Books; Illustrated edition   
3          Tor Books; Illustrated edition   
4      Bloomsbury Publishing; 1st edition   
...                                   ...   
82511                 Copper Canyon Press   
82512                 Copper Canyon Press   
82513                 Copper Canyon Press   
82514                 Copper Canyon Press   
82515                 Copper Canyon Press   

                                                 img_url  label  \
0      https://images-na.ssl-images-amazon.com/images...      2   
1      https://images-na.ssl-images-amazon.com/images...      2   
2      https://images-na.ssl-images-amazon.com/images...      5   
3      https://images-na.ssl-images-amazon.com/images...      1   
4      https://images-na.ssl-images-amazon.com/images...      4   
...                                                  ...    ...   
82511  https://images-na.ssl-images-amazon.com/images...      5   
82512  https://images-na.ssl-images-amazon.com/images...      4   
82513  https://images-na.ssl-images-amazon.com/images...      2   
82514  https://images-na.ssl-images-amazon.com/images...      5   
82515  https://images-na.ssl-images-amazon.com/images...      5   

                                            id  
0      51FVPBt51ZL._SX329_BO1,204,203,200_.jpg  
1      51FVPBt51ZL._SX329_BO1,204,203,200_.jpg  
2      51FVPBt51ZL._SX329_BO1,204,203,200_.jpg  
3      51FVPBt51ZL._SX329_BO1,204,203,200_.jpg  
4      51nYjtfGQnL._SY344_BO1,204,203,200_.jpg  
...                                        ...  
82511  51qAZy-xFtL._SY344_BO1,204,203,200_.jpg  
82512  51qAZy-xFtL._SY344_BO1,204,203,200_.jpg  
82513  51qAZy-xFtL._SY344_BO1,204,203,200_.jpg  
82514  51qAZy-xFtL._SY344_BO1,204,203,200_.jpg  
82515  51qAZy-xFtL._SY344_BO1,204,203,200_.jpg  

[82516 rows x 8 columns]

In [12]:
df["objects"]=""
df["scores"]=""
df

number                                             review  \
0           0  hollow ever gone tourist thinking finally goin...   
1           1  monotonous dragging pace feel like reading boo...   
2           2  much complex romance human devil act larue mak...   
3           3  invisible interest bought book based bought bo...   
4           4  even though really wish book wa solidly good y...   
...       ...                                                ...   
82511   82511  naked raw cover tricked read lot anthology tho...   
82512   82512  better le great buying book based love poetry ...   
82513   82513  picked book fell love book feel like came sike...   
82514   82514  much like crush think volume going stay much l...   
82515   82515  siken incredible follow poetry siken incredibl...   

                                                   title         author  \
0                      The Invisible Life of Addie LaRue   V. E. Schwab   
1                      The Invisible Life of Addie LaRue   V. E. Schwab   
2                      The Invisible Life of Addie LaRue   V. E. Schwab   
3                      The Invisible Life of Addie LaRue   V. E. Schwab   
4      A Court of Silver Flames (A Court of Thorns an...  Sarah J. Maas   
...                                                  ...            ...   
82511                                   War of the Foxes  Richard Siken   
82512                                   War of the Foxes  Richard Siken   
82513                                   War of the Foxes  Richard Siken   
82514                                   War of the Foxes  Richard Siken   
82515                                   War of the Foxes  Richard Siken   

                                publisher  \
0          Tor Books; Illustrated edition   
1          Tor Books; Illustrated edition   
2          Tor Books; Illustrated edition   
3          Tor Books; Illustrated edition   
4      Bloomsbury Publishing; 1st edition   
...                                   ...   
82511                 Copper Canyon Press   
82512                 Copper Canyon Press   
82513                 Copper Canyon Press   
82514                 Copper Canyon Press   
82515                 Copper Canyon Press   

                                                 img_url  label  \
0      https://images-na.ssl-images-amazon.com/images...      2   
1      https://images-na.ssl-images-amazon.com/images...      2   
2      https://images-na.ssl-images-amazon.com/images...      5   
3      https://images-na.ssl-images-amazon.com/images...      1   
4      https://images-na.ssl-images-amazon.com/images...      4   
...                                                  ...    ...   
82511  https://images-na.ssl-images-amazon.com/images...      5   
82512  https://images-na.ssl-images-amazon.com/images...      4   
82513  https://images-na.ssl-images-amazon.com/images...      2   
82514  https://images-na.ssl-images-amazon.com/images...      5   
82515  https://images-na.ssl-images-amazon.com/images...      5   

                                            id objects scores  
0      51FVPBt51ZL._SX329_BO1,204,203,200_.jpg                 
1      51FVPBt51ZL._SX329_BO1,204,203,200_.jpg                 
2      51FVPBt51ZL._SX329_BO1,204,203,200_.jpg                 
3      51FVPBt51ZL._SX329_BO1,204,203,200_.jpg                 
4      51nYjtfGQnL._SY344_BO1,204,203,200_.jpg                 
...                                        ...     ...    ...  
82511  51qAZy-xFtL._SY344_BO1,204,203,200_.jpg                 
82512  51qAZy-xFtL._SY344_BO1,204,203,200_.jpg                 
82513  51qAZy-xFtL._SY344_BO1,204,203,200_.jpg                 
82514  51qAZy-xFtL._SY344_BO1,204,203,200_.jpg                 
82515  51qAZy-xFtL._SY344_BO1,204,203,200_.jpg                 

[82516 rows x 10 columns]

In [13]:
labelscore_file = "img_labelscore_dict.json"

with open(labelscore_file,"r") as f:
    label_dict=json.load(f)

In [14]:
label_dict

{'51FVPBt51ZL._SX329_BO1,204,203,200_.jpg': [['', '', '', '', ''],
  [0, 0, 0, 0, 0]],
 '51nYjtfGQnL._SY344_BO1,204,203,200_.jpg': [['', '', '', '', ''],
  [0, 0, 0, 0, 0]],
 '41qI9quGIdL._SY344_BO1,204,203,200_.jpg': [['', '', '', '', ''],
  [0, 0, 0, 0, 0]],
 '51c47I+qyAL._SX479_BO1,204,203,200_.jpg': [['book', '', '', '', ''],
  [84.08278822898865, 0, 0, 0, 0]],
 '61ELLOaoSZL._SX379_BO1,204,203,200_.jpg': [['', '', '', '', ''],
  [0, 0, 0, 0, 0]],
 '41-p5bsEBUL._SY344_BO1,204,203,200_.jpg': [['', '', '', '', ''],
  [0, 0, 0, 0, 0]],
 '51TeiVYTKXL._SX329_BO1,204,203,200_.jpg': [['person', '', '', '', ''],
  [66.67532324790955, 0, 0, 0, 0]],
 '51LmtX5KPAL._SX406_BO1,204,203,200_.jpg': [['dog', '', '', '', ''],
  [74.04384016990662, 0, 0, 0, 0]],
 '51vhXIpJE3L._SX330_BO1,204,203,200_.jpg': [['person', 'person', '', '', ''],
  [94.80453133583069, 86.52041554450989, 0, 0, 0]],
 '51nCu9L17gL._SY344_BO1,204,203,200_.jpg': [['', '', '', '', ''],
  [0, 0, 0, 0, 0]],
 '61Yy8KB8O1L._SX380_BO1,

In [15]:
for ind, d in enumerate(df.id):
    print(label_dict[d])
    df["objects"].iloc[ind]=label_dict[d][0]
    df["scores"].iloc[ind]=label_dict[d][1]

[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['book', '', '', '', ''], [84.08278822898865, 0, 0, 0, 0]]
[['book', '', '', '', ''], [84.08278822898865, 0, 0, 0, 0]]
[['book', '', '', '', ''], [84.08278822898865, 0, 0, 0, 0]]
[['book', '', '', '', ''], [84.08278822898865, 0, 0, 0, 0]]
[['book', '', '', '', ''], [84.08278822898865, 0, 0, 0, 0]]
[['book', '', '', '', ''], [84.08278822898865, 0, 0, 0, 0]]
[['book', '', '', '', ''], [84.08278822898865, 0, 0, 0, 0]]
[['book', '', '', '', ''], [84.08278822898865, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]


[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]


[['bird', '', '', '', ''], [64.2651379108429, 0, 0, 0, 0]]
[['bird', '', '', '', ''], [64.2651379108429, 0, 0, 0, 0]]
[['person', '', '', '', ''], [99.55512881278992, 0, 0, 0, 0]]
[['person', '', '', '', ''], [99.55512881278992, 0, 0, 0, 0]]
[['person', '', '', '', ''], [99.55512881278992, 0, 0, 0, 0]]
[['person', '', '', '', ''], [99.55512881278992, 0, 0, 0, 0]]
[['person', '', '', '', ''], [99.55512881278992, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['person', '', '', '', ''], [97.85866141319275, 0, 0, 0, 0]]
[['person', '', '', '', ''], [97.85866141319275, 0, 0, 0, 0]]
[['person', '', '', '', ''], [97.85866141319275, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0,

[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['person', '', '', '', ''], [96.20298743247986, 0, 0, 0, 0]]
[['person', '', ''

[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['person', '', '', '', ''], [69.30838823318481, 0, 0, 0, 0]]
[['person', '', '', '', ''], [69.30838823318481, 0, 0, 0, 0]]
[['person', '', '', '', ''], [69.30838823318481, 0, 0, 0, 0]]
[['person', '', '', '', ''], [69.30838823318481, 0, 0, 0, 0]]
[['person', '', '', '', ''], [69.30838823318481, 0, 0, 0, 0]]
[['person', '', '', '', ''], [69.30838823318481, 0, 0, 0, 0]]
[['person', '', '', '', ''], [69.30838823318481, 0, 0, 0, 0]]
[['person', '', '', '', ''], [94.89577412605286, 0, 0, 0, 0]]
[['person', '', '', '', ''], [94.89577412605286, 0, 0, 0, 0]]
[['person', '', '', '', ''], [94.89577412605286, 0, 0, 0, 0]]
[['person', '', '', '', ''], [94.89577412605286, 0, 0, 0, 0]]
[['person', '', '', '', ''], [94.89577

...

[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]


[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]


[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['person', '', '', '', ''], [85.11871695518494, 0, 0, 0, 0]]
[['person', '', '', '', ''], [85.11871695518494, 0, 0, 0, 0]]
[['person', '', '', '', ''], [97.84309267997742, 0, 0, 0, 0]]
[['person', '', '', '', ''], [97.84309267997742, 0, 0, 0, 0]]
[['person', '', '', '', ''], [97.84309267997742, 0, 0, 0, 0]]
[['person', '', '', '', ''], [97.84309267997742, 0, 0, 0, 0]]
[['person', '', '', '', ''], [97.84309267997742, 0, 0, 0, 0]]
[['person', '', '', '', ''], [97.84309267997742, 0, 0, 0, 0]]
[['person', '', '', '', ''], [97.84309267997742, 0, 0, 0, 0]]
[['person', '', '', '', ''], [97.84309267997742, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''

[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['person', '', '', '', ''], [63.03458213806152, 0, 0, 0, 0]]
[['person', '', '', '', ''], [63.03458213806152, 0, 0, 0, 0]]
[['person', '', '', '', ''], [63.03458213806152, 0, 0, 0, 0]]
[['person', '', '', '', ''], [63.03458213806152, 0, 0, 0, 0]]
[['person', '', '', '', ''], [63.03458213806152, 0, 0, 0, 0]]
[['person', '', '', '', ''], [63.03458213806152, 0

[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]
[['', '', '', '', ''], [0, 0, 0, 0, 0]]


In [16]:
df

number                                             review  \
0           0  hollow ever gone tourist thinking finally goin...   
1           1  monotonous dragging pace feel like reading boo...   
2           2  much complex romance human devil act larue mak...   
3           3  invisible interest bought book based bought bo...   
4           4  even though really wish book wa solidly good y...   
...       ...                                                ...   
82511   82511  naked raw cover tricked read lot anthology tho...   
82512   82512  better le great buying book based love poetry ...   
82513   82513  picked book fell love book feel like came sike...   
82514   82514  much like crush think volume going stay much l...   
82515   82515  siken incredible follow poetry siken incredibl...   

                                                   title         author  \
0                      The Invisible Life of Addie LaRue   V. E. Schwab   
1                      The Invisible Life of Addie LaRue   V. E. Schwab   
2                      The Invisible Life of Addie LaRue   V. E. Schwab   
3                      The Invisible Life of Addie LaRue   V. E. Schwab   
4      A Court of Silver Flames (A Court of Thorns an...  Sarah J. Maas   
...                                                  ...            ...   
82511                                   War of the Foxes  Richard Siken   
82512                                   War of the Foxes  Richard Siken   
82513                                   War of the Foxes  Richard Siken   
82514                                   War of the Foxes  Richard Siken   
82515                                   War of the Foxes  Richard Siken   

                                publisher  \
0          Tor Books; Illustrated edition   
1          Tor Books; Illustrated edition   
2          Tor Books; Illustrated edition   
3          Tor Books; Illustrated edition   
4      Bloomsbury Publishing; 1st edition   
...                                   ...   
82511                 Copper Canyon Press   
82512                 Copper Canyon Press   
82513                 Copper Canyon Press   
82514                 Copper Canyon Press   
82515                 Copper Canyon Press   

                                                 img_url  label  \
0      https://images-na.ssl-images-amazon.com/images...      2   
1      https://images-na.ssl-images-amazon.com/images...      2   
2      https://images-na.ssl-images-amazon.com/images...      5   
3      https://images-na.ssl-images-amazon.com/images...      1   
4      https://images-na.ssl-images-amazon.com/images...      4   
...                                                  ...    ...   
82511  https://images-na.ssl-images-amazon.com/images...      5   
82512  https://images-na.ssl-images-amazon.com/images...      4   
82513  https://images-na.ssl-images-amazon.com/images...      2   
82514  https://images-na.ssl-images-amazon.com/images...      5   
82515  https://images-na.ssl-images-amazon.com/images...      5   

                                            id     objects           scores  
0      51FVPBt51ZL._SX329_BO1,204,203,200_.jpg  [, , , , ]  [0, 0, 0, 0, 0]  
1      51FVPBt51ZL._SX329_BO1,204,203,200_.jpg  [, , , , ]  [0, 0, 0, 0, 0]  
2      51FVPBt51ZL._SX329_BO1,204,203,200_.jpg  [, , , , ]  [0, 0, 0, 0, 0]  
3      51FVPBt51ZL._SX329_BO1,204,203,200_.jpg  [, , , , ]  [0, 0, 0, 0, 0]  
4      51nYjtfGQnL._SY344_BO1,204,203,200_.jpg  [, , , , ]  [0, 0, 0, 0, 0]  
...                                        ...         ...              ...  
82511  51qAZy-xFtL._SY344_BO1,204,203,200_.jpg  [, , , , ]  [0, 0, 0, 0, 0]  
82512  51qAZy-xFtL._SY344_BO1,204,203,200_.jpg  [, , , , ]  [0, 0, 0, 0, 0]  
82513  51qAZy-xFtL._SY344_BO1,204,203,200_.jpg  [, , , , ]  [0, 0, 0, 0, 0]  
82514  51qAZy-xFtL._SY344_BO1,204,203,200_.jpg  [, , , , ]  [0, 0, 0, 0, 0]  
82515  51qAZy-xFtL._SY344_BO1,204,203,200_.jpg  [, , , , ]  [0, 0, 0, 0, 0]  

[82516

In [17]:
cut_length = 1

obj_list, score_list = [],[]
for t in df[["objects","scores"]].values:
    obj, scr = t[0], t[1]
    obj_list.append(obj[:cut_length])
    score_list.append(scr[:cut_length])

In [18]:
obj_list, score_list = np.array(obj_list), np.array(score_list)

In [19]:
from sklearn.preprocessing import OneHotEncoder

In [20]:
ohe = OneHotEncoder()

In [21]:
obj_ohe = ohe.fit(obj_list).transform(obj_list).toarray()

In [22]:
obj_ohe.shape

(82516, 59)

In [23]:
obj = obj_ohe*score_list*0.01
obj

array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

In [24]:
obj.shape

(82516, 59)

In [25]:
# review, number, label 값 저장
review = df['review'].values.astype(str)
title = df["title"].values.astype(str)
author = df["author"].values.astype(str)
publisher = df["publisher"].values.astype(str)
number = df['number'].values
label = df['label'].values

In [26]:
maxlen = 100
nEmbeddingDim = 128
neurons = 128
epochs = 50
kernel_size = 5
filters = 32 #64
pool_size = 4

batch_size = 32

soft, hard = resource.getrlimit(resource.RLIMIT_NOFILE)
resource.setrlimit(resource.RLIMIT_NOFILE, (hard, hard))

In [27]:
InputSize_wh = 32

In [28]:
import pickle, os
imgarray_filename = 'book_dataset{}/imgarray.pickle'.format(InputSize_wh)
print(imgarray_filename)

book_dataset32/imgarray.pickle


In [29]:
if os.path.isfile(imgarray_filename):
    print("파일이 존재합니다.")
    with open(imgarray_filename, 'rb') as fp:
        num2resizedImg = pickle.load(fp)
    print("불러온 data #: {}".format(len(num2resizedImg)))
else:
    print("파일을 생성합니다")
    
    # 시스템 내의 이미지 디렉토리의 리스트
    imagedirs = os.listdir('book_dataset')
    imagedirs.remove(".ipynb_checkpoints")

    # number를 key값, image를 value값으로 하는 dict 파일(num2img) 생성
    num2img = {}
    for num in df['number'][:]:
        img = Image.open('book_dataset/' + df['id'][num])
        num2img[num] = img

    # input size 지정
    InputSize = (InputSize_wh, InputSize_wh)

    ImageFile.LOAD_TRUNCATED_IMAGES = True

    # image를 array로 변환해 저장
    num2resizedImg = {}
    for key,value in num2img.items():
        if value != None:
            num2resizedImg[key] = np.array(value.resize(InputSize),dtype=np.float)/255.0
        else:
            num2resizedImg[key] = None

    # 채널 1개인 이미지를 3개로 변환
    for i in range(len(number)):
        if num2resizedImg[i].shape != (InputSize_wh, InputSize_wh, 3):
            # normalize
            norm = cv2.normalize(num2resizedImg[i], None, alpha=0, beta=255, norm_type=cv2.NORM_MINMAX, dtype=cv2.CV_8U)
            # convert to 3 channel
            num2resizedImg[i] = cv2.cvtColor(norm, cv2.COLOR_GRAY2BGR)
            
    with open(imgarray_filename, 'wb') as fp:
        pickle.dump(num2resizedImg, fp)

### data loader 구현
class ReviewCoverLoader(tf.keras.utils.Sequence):
    def __init__(self, number, review, imageDict, objects, y_label, batch_size, shuffle = True,outputShape = None):
        # X:np.ndarray liwc vectors + hotel names + reviewr score 
        # imageDict: hotelname2images dict 
        self.number = number
        self.review = review
        self.imageDict = imageDict
        self.objects = objects
        self.y_label = y_label
        self.batch_size = batch_size
        self.shuffle = shuffle
        self.outputShape = outputShape
        self.on_epoch_end()

    def on_epoch_end(self):
        self.indexes = np.arange(self.review.shape[0])
        if self.shuffle:
            np.random.shuffle(self.indexes)

    def __len__(self):
        return int(np.floor(self.review.shape[0] / self.batch_size))


    def __getitem__(self, index):
        indexes = self.indexes[index * self.batch_size : (index + 1) * self.batch_size]

        #hotelnames = self.hotelnames[indexes]
        review = self.review[indexes]
        objects = self.objects[indexes]
        #hotelinfo = self.hotelinfo[indexes]
        y = self.y_label[indexes]
        number = self.number[indexes]

        images = np.zeros(shape=(len(number), InputSize_wh, InputSize_wh, 3),dtype=np.float)
    #   images = np.zeros(shape=(len(hotelnames),7,7,512),dtype=np.float)
        for i in range(len(number)):
            images[i] = self.imageDict[i]
            #images[i] = self.imageDict[hotelnames[i].strip()]
    #       images[i] = f_out.get(hotelnames[i])

        return [review, images, objects],y

파일이 존재합니다.
불러온 data #: 82516


In [30]:
total_result = pd.DataFrame()
accuracy_avg = 0

In [31]:
for ind, (train_index, test_index) in enumerate(kf.split(review)):
    print("\n{}{}th {}".format("-"*20,ind+1,"-"*20))
    train_number, train_review, train_title, train_author, train_publisher, train_obj, train_label = number[train_index], review[train_index], title[train_index], author[train_index], publisher[train_index], obj[train_index], label[train_index]
    test_number, test_review, test_title, test_author, test_publisher, test_obj, test_label = number[test_index], review[test_index], title[test_index], author[test_index], publisher[test_index], obj[test_index], label[test_index]
    valid_number, test_number, valid_review, test_review, valid_title, test_title, valid_author, test_author, valid_publisher, test_publisher, valid_obj, test_obj, valid_label, test_label = train_test_split(test_number, test_review, test_title, test_author, test_publisher, test_obj, test_label, test_size=.5)
    
    print("total #: {}".format(len(review)))
    print("train #: {}".format(len(train_review)))
    print("valid #: {}".format(len(valid_review)))
    print("test #: {}".format(len(test_review)))
    
    # review 데이터 tokenizing
    tokenizer = tf.keras.preprocessing.text.Tokenizer()
    tokenizer.fit_on_texts(train_review)
    sequencesTrain = tokenizer.texts_to_sequences(train_review)
    sequencesValid = tokenizer.texts_to_sequences(valid_review)
    sequencesTest = tokenizer.texts_to_sequences(test_review)
    
    # vocab_size 계산
    vocab_size = len(tokenizer.word_index)+1
    
    # preprocessing
    maxlen = 100
    pad_Train = tf.keras.preprocessing.sequence.pad_sequences(sequencesTrain, maxlen=maxlen)
    pad_Valid = tf.keras.preprocessing.sequence.pad_sequences(sequencesValid, maxlen=maxlen)
    pad_Test = tf.keras.preprocessing.sequence.pad_sequences(sequencesTest, maxlen=maxlen)
    
    # title 데이터 tokenizing, preprocessing
    title_tokenizer = tf.keras.preprocessing.text.Tokenizer()
    title_tokenizer.fit_on_texts(train_title)
    title_sequencesTrain = title_tokenizer.texts_to_sequences(train_title)
    title_sequencesValid = title_tokenizer.texts_to_sequences(valid_title)
    title_sequencesTest = title_tokenizer.texts_to_sequences(test_title)
    
    t = np.array([len(a) for a in title_sequencesTrain]).max()
    
    title_pad_Train = tf.keras.preprocessing.sequence.pad_sequences(title_sequencesTrain, maxlen=t)
    title_pad_Valid = tf.keras.preprocessing.sequence.pad_sequences(title_sequencesValid, maxlen=t)
    title_pad_Test = tf.keras.preprocessing.sequence.pad_sequences(title_sequencesTest, maxlen=t)
    
    # author 데이터 tokenizing, preprocessing
    author_tokenizer = tf.keras.preprocessing.text.Tokenizer()
    author_tokenizer.fit_on_texts(train_author)
    author_sequencesTrain = author_tokenizer.texts_to_sequences(train_author)
    author_sequencesValid = author_tokenizer.texts_to_sequences(valid_author)
    author_sequencesTest = author_tokenizer.texts_to_sequences(test_author)
    
    a = np.array([len(a) for a in author_sequencesTrain]).max()
    
    author_pad_Train = tf.keras.preprocessing.sequence.pad_sequences(author_sequencesTrain, maxlen=a)
    author_pad_Valid = tf.keras.preprocessing.sequence.pad_sequences(author_sequencesValid, maxlen=a)
    author_pad_Test = tf.keras.preprocessing.sequence.pad_sequences(author_sequencesTest, maxlen=a)
    
    # publisher 데이터 tokenizing, preprocessing
    publisher_tokenizer = tf.keras.preprocessing.text.Tokenizer()
    publisher_tokenizer.fit_on_texts(train_publisher)
    publisher_sequencesTrain = publisher_tokenizer.texts_to_sequences(train_publisher)
    publisher_sequencesValid = publisher_tokenizer.texts_to_sequences(valid_publisher)
    publisher_sequencesTest = publisher_tokenizer.texts_to_sequences(test_publisher)
    
    p = np.array([len(a) for a in publisher_sequencesTrain]).max()
    
    publisher_pad_Train = tf.keras.preprocessing.sequence.pad_sequences(publisher_sequencesTrain, maxlen=p)
    publisher_pad_Valid = tf.keras.preprocessing.sequence.pad_sequences(publisher_sequencesValid, maxlen=p)
    publisher_pad_Test = tf.keras.preprocessing.sequence.pad_sequences(publisher_sequencesTest, maxlen=p)
    
    # review + title + author + publisher concat
    pad_Train = np.concatenate((pad_Train,title_pad_Train,author_pad_Train,publisher_pad_Train),axis=1)
    pad_Valid = np.concatenate((pad_Valid,title_pad_Valid,author_pad_Valid,publisher_pad_Valid),axis=1)
    pad_Test = np.concatenate((pad_Test,title_pad_Test,author_pad_Test,publisher_pad_Test),axis=1)
    
    print(pad_Train.shape)
    print(pad_Valid.shape)
    print(pad_Test.shape)
    
    total_len = pad_Train.shape[1]
    
    tf.keras.backend.clear_session()
    
    ####################
    # review+meta flow #
    ####################
    
    # review flow 
    reviewInputTensor = tf.keras.layers.Input(shape=(total_len,))
    reviewFlow = tf.keras.layers.Embedding(vocab_size
                                       ,nEmbeddingDim,input_length=maxlen)(reviewInputTensor)
    reviewFlow = tf.keras.layers.Dropout(0.25)(reviewFlow)
    reviewFlow = tf.keras.layers.Conv1D(filters
                    ,kernel_size,padding='valid',activation='relu',strides=1)(reviewFlow)
    reviewFlow = tf.keras.layers.MaxPool1D(pool_size = pool_size)(reviewFlow)
    
    # reviewFlow = tf.keras.layers.LSTM(64)(reviewFlow)
    
    reviewFlow = tf.keras.layers.Flatten()(reviewFlow)
#     reviewFlow = tf.keras.layers.Dense(512,activation='relu')(reviewFlow)
#     reviewFlow = tf.keras.layers.BatchNormalization()(reviewFlow)
    reviewFlow = tf.keras.layers.Dense(256,activation='relu')(reviewFlow)
#     reviewFlow = tf.keras.layers.BatchNormalization()(reviewFlow)
#     reviewFlow = tf.keras.layers.Dense(128,activation='relu')(reviewFlow)
#     reviewFlow = tf.keras.layers.Dense(64,activation='relu')(reviewFlow)
    #softmax = tf.keras.layers.Dense(6,activation='softmax')(reviewFlow)
    
    ###############
    # image flow #
    ##############
    
    # image flow 
    imageInputTensor = tf.keras.layers.Input(shape=(InputSize_wh, InputSize_wh, 3))

    imgflow = tf.keras.layers.Conv2D(32,(3,3),padding='same',activation = 'relu')(imageInputTensor)
    imgflow = tf.keras.layers.Conv2D(32,(3,3),padding='same',activation = 'relu')(imgflow)
    imgflow = tf.keras.layers.MaxPooling2D(pool_size=(4,4))(imgflow)
    imgflow = tf.keras.layers.Dropout(0.25)(imgflow)

#     imgflow = tf.keras.layers.Conv2D(32,(3,3),padding='same',activation = 'relu')(imgflow)
#     imgflow = tf.keras.layers.MaxPooling2D(pool_size=(4,4))(imgflow)
#     imgflow = tf.keras.layers.Dropout(0.25)(imgflow)

#     imgflow = tf.keras.layers.Conv2D(32,(3,3),padding='same',activation = 'relu')(imgflow)
#     imgflow = tf.keras.layers.Dropout(0.25)(imgflow)

#     imgflow = tf.keras.layers.Conv2D(32,(3,3),padding='same',activation = 'relu')(imgflow)
#     imgflow = tf.keras.layers.Dropout(0.25)(imgflow)

    imgflow = tf.keras.layers.Flatten()(imgflow)
    imgflow = tf.keras.layers.Dense(512,activation='relu')(imgflow)
    imgflow = tf.keras.layers.BatchNormalization()(imgflow)
    imgflow = tf.keras.layers.Dense(256,activation='relu')(imgflow)
    imgflow = tf.keras.layers.BatchNormalization()(imgflow)
    imgflow = tf.keras.layers.Dense(128,activation='relu')(imgflow)
    imgflow = tf.keras.layers.Dense(64,activation='relu')(imgflow)
    
    ###############
    # object flow #
    ##############
    
    # object flow
    objectInputTensor = tf.keras.layers.Input(shape=(obj.shape[1],))
    objectflow = tf.keras.layers.Dense(32,activation='relu')(objectInputTensor)
#     objectflow = tf.keras.layers.BatchNormalization()(objectflow)
#     objectflow = tf.keras.layers.Dense(32,activation='relu')(objectflow)
    
    ###############
    # concat flow #
    ##############
    
    # concat

    flow = tf.keras.layers.concatenate(inputs=[reviewFlow,imgflow, objectflow])
    # flow = reviewFlow
#     flow = tf.keras.layers.Dense(512,activation='relu')(flow)
#     flow = tf.keras.layers.BatchNormalization()(flow)
#     flow = tf.keras.layers.Dense(512,activation='relu')(flow)
#     flow = tf.keras.layers.BatchNormalization()(flow)
#     flow = tf.keras.layers.Dense(64,activation='relu')(flow)
    softmax = tf.keras.layers.Dense(6,activation='softmax')(flow)

    model = tf.keras.Model(inputs=[reviewInputTensor,imageInputTensor,objectInputTensor],
                          outputs=[softmax])
    
    class_weights = class_weight.compute_class_weight('balanced', np.unique(train_label), train_label)
    print('\nClass Weight: {}\n'.format(class_weights))
    
    adam = tf.keras.optimizers.Adam(lr=0.0009, beta_1=0.9, beta_2=0.999, epsilon=None, decay=0.0, amsgrad=False)
    
    # model compile
    model.compile(loss=tf.keras.losses.sparse_categorical_crossentropy,
              optimizer=adam,
              metrics=['accuracy'])
    
    checkpoint_file = "504-checkpoint_21.h5"
    callback = tf.keras.callbacks.EarlyStopping(
                                monitor='val_loss', 
                                patience = 3)
    
    checkpoint = tf.keras.callbacks.ModelCheckpoint(
                            checkpoint_file,             # file명을 지정합니다
                             monitor='val_loss',   # val_loss 값이 개선되었을때 호출됩니다
                              verbose=1,            # 로그를 출력합니다
                             save_best_only=True,  # 가장 best 값만 저장합니다
                            save_weights_only=True,
                             mode='auto'           
                            )
    
    # model fit
    print("batch size: {}".format(batch_size))
    model.fit_generator(
#     verbose = 1,
    generator = ReviewCoverLoader(train_number,pad_Train,num2resizedImg,train_obj,train_label,batch_size), 
    validation_data = ReviewCoverLoader(valid_number,pad_Valid, num2resizedImg, valid_obj, valid_label, batch_size),
#     validation_steps=len(valid_label)//batch_size,
    epochs = epochs,
    callbacks=[callback,checkpoint],
    workers=10, use_multiprocessing=True, class_weight=class_weights)
    
    model.load_weights(checkpoint_file)
    
    fused_predict = model.predict_generator(ReviewCoverLoader(
        test_number,pad_Test,num2resizedImg,test_obj,test_label,batch_size,shuffle=False))
    report_score = classification_report(test_label[:len(fused_predict)], fused_predict.argmax(axis=1),digits=4, output_dict=True)
    accuracy_avg+=report_score["accuracy"]
    report_score = pd.DataFrame(report_score)
    
    if(ind==0):total_result = report_score
    else:total_result += report_score
    
    print('\n',report_score.T)
    print()


--------------------1th --------------------
total #: 82516
train #: 66012
valid #: 8252
test #: 8252
(66012, 188)
(8252, 188)
(8252, 188)
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor
Instructions for updating:
If using Keras pass *_constraint arguments to layers.

Class Weight: [3.13001422 4.15300409 2.46866118 1.3141947  0.30546262]

batch size: 32
Epoch 1/50
 246/2062 [==>...........................] - ETA: 28s - loss: 0.7908 - acc: 0.7001
Epoch 00001: val_loss improved from inf to 0.79180, saving model to 504-checkpoint_21.h5
2062/2062 [==============================] - 21s 10ms/step - loss: 0.8229 - acc: 0.6971 - val_loss: 0.7918 - val_acc: 0.6997
Epoch 2/50
 244/2062 [==>...........................] - ETA: 28s - loss: 0.8109 - acc: 0.6821
Epoch 00002: val_loss did not improve from 0.79180
2062/2062 [==============================] - 18s 9ms/step - loss: 0.6128 - acc: 0.7640 - val_loss: 0.8152 - val_acc: 0.6

 244/2062 [==>...........................] - ETA: 27s - loss: 0.7985 - acc: 0.6849
Epoch 00002: val_loss did not improve from 0.75080
2062/2062 [==============================] - 18s 9ms/step - loss: 0.6148 - acc: 0.7632 - val_loss: 0.8015 - val_acc: 0.6843
Epoch 3/50
 245/2062 [==>...........................] - ETA: 27s - loss: 0.9407 - acc: 0.6730
Epoch 00003: val_loss did not improve from 0.75080
2062/2062 [==============================] - 18s 9ms/step - loss: 0.4174 - acc: 0.8420 - val_loss: 0.9422 - val_acc: 0.6722
Epoch 4/50
 246/2062 [==>...........................] - ETA: 26s - loss: 1.2567 - acc: 0.6819
Epoch 00004: val_loss did not improve from 0.75080
2062/2062 [==============================] - 18s 9ms/step - loss: 0.2615 - acc: 0.9028 - val_loss: 1.2552 - val_acc: 0.6807

               precision    recall  f1-score      support
1              0.539130  0.595200  0.565779   625.000000
2              0.360731  0.170259  0.231332   464.000000
3              0.435897  0.3112

In [32]:
print("평균 accuracy: ",accuracy_avg/num)

평균 accuracy:  0.7141293774319066


In [33]:
f_name = "{}.csv".format(time.ctime())
total_result.to_csv(f_name,index=True)
print(f_name)

Thu Aug 26 05:58:24 2021.csv


In [34]:
total_result/num

1           2           3            4            5  \
precision    0.520025    0.340316    0.378138     0.456694     0.784017   
recall       0.636588    0.092880    0.222831     0.202574     0.950869   
f1-score     0.571321    0.139145    0.278960     0.276578     0.859212   
support    557.400000  403.400000  678.200000  1249.000000  5336.000000   

           accuracy    macro avg  weighted avg  
precision  0.714129     0.495838      0.662040  
recall     0.714129     0.421148      0.714129  
f1-score   0.714129     0.425043      0.668677  
support    0.714129  8224.000000   8224.000000